In [1]:
# Cargando las librerias necesarias
import pandas as pd
import numpy as np
from datasets import load_dataset
from transformers import AutoTokenizer
from transformers import DataCollatorForSeq2Seq
import evaluate
from transformers import AutoModelForSeq2SeqLM, Seq2SeqTrainingArguments, Seq2SeqTrainer
import numpy as np
from datasets import load_metric
from huggingface_hub import notebook_login
from transformers import pipeline
from huggingface_hub import create_repo

notebook_login()


In [11]:
repo_id = "spanish_to_ayuuk_translator"           
organization = "l52mas"       

create_repo(
    repo_id=f"{organization}/{repo_id}", 
    repo_type="model",                  
    exist_ok=True                        
)

RepoUrl('https://huggingface.co/l52mas/spanish_to_ayuuk_translator', endpoint='https://huggingface.co', repo_type='model', repo_id='l52mas/spanish_to_ayuuk_translator')

In [2]:
# Leemos los corpus de la biblia y de Delfino
bible_data = pd.read_csv('full_corpus_bible.csv')
bible_index = pd.read_csv('full_corpus_index.csv')

# Unimos ambos corpus y reseteamos los indices
bible_data = pd.concat([bible_data, bible_index], axis=0)
bible_data['id'] = range(0, len(bible_data))

# Guardamos el corpus final
bible_data.to_csv('bible_and_corpus1.csv', index=False)

In [3]:
# Transformamos el corpus en un dataset de HuggingFace
dataset = load_dataset('csv', data_files='bible_and_corpus1.csv', column_names=['spanish', 'ayuuk', 'id'])

# Lo transformamos al formato necesario para el entrenamiento
dataset = dataset.map(lambda x: {'translation': {'es': x['spanish'], 'ayuuk': x['ayuuk']}, 'id': x['id']})
dataset = dataset.remove_columns(['spanish', 'ayuuk'])

# Dividimos el dataset en entrenamiento y validación
dataset = dataset['train'].train_test_split(test_size=0.15)
dataset

Generating train split: 0 examples [00:00, ? examples/s]

Map:   0%|          | 0/10076 [00:00<?, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['id', 'translation'],
        num_rows: 8564
    })
    test: Dataset({
        features: ['id', 'translation'],
        num_rows: 1512
    })
})

In [4]:
# Cargamos el modelo preentrenado
checkpoint = "google-t5/t5-small"
tokenizer = AutoTokenizer.from_pretrained(checkpoint)

In [5]:
source_lang = "es"
target_lang = "ayuuk"
prefix = "translate Spanish to Ayuuk: "

# Tranformamos los inputs al formato:
# translate Spanish to Ayuuk: texto en español
def preprocess_function(examples):
    inputs = [prefix + example[source_lang] for example in examples["translation"]]
    targets = [example[target_lang] for example in examples["translation"]]
    model_inputs = tokenizer(inputs, text_target=targets, max_length=128, truncation=True)
    return model_inputs

#tokenized_corpus = dataset.map(preprocess_function, batched=True)
tokenized_corpus = dataset.map(preprocess_function, batched=True)

Map:   0%|          | 0/8564 [00:00<?, ? examples/s]

Map:   0%|          | 0/1512 [00:00<?, ? examples/s]

In [6]:
data_collator = DataCollatorForSeq2Seq(tokenizer=tokenizer, model=checkpoint)
metric = evaluate.load("sacrebleu")
cer_metric = load_metric("cer")
wer_metric = load_metric("wer")


# Función para evaluar el modelo
def postprocess_text(preds, labels):
    preds = [pred.strip() for pred in preds]
    labels = [[label.strip()] for label in labels]

    return preds, labels

# Función que calcula bleu, cer y wer
def compute_metrics(eval_preds):
    preds, labels = eval_preds
    if isinstance(preds, tuple):
        preds = preds[0]
    decoded_preds = tokenizer.batch_decode(preds, skip_special_tokens=True)

    labels = np.where(labels != -100, labels, tokenizer.pad_token_id)
    decoded_labels = tokenizer.batch_decode(labels, skip_special_tokens=True)

    decoded_preds, decoded_labels = postprocess_text(decoded_preds, decoded_labels)

    result = metric.compute(predictions=decoded_preds, references=decoded_labels)
    cer = cer_metric.compute(predictions=decoded_preds, references=decoded_labels)
    result["cer"] = cer
    
    wer =  wer_metric.compute(predictions=decoded_preds, references=decoded_labels)
    result["wer"] = wer
    
    result = {"bleu": result["score"], "cer": result["cer"], "wer": result["wer"]}

    prediction_lens = [np.count_nonzero(pred != tokenizer.pad_token_id) for pred in preds]
    result["gen_len"] = np.mean(prediction_lens)
    result = {k: round(v, 4) for k, v in result.items()}
    return result

C:\Users\olver\AppData\Local\Temp\ipykernel_3180\3890291550.py:3: FutureWarning: load_metric is deprecated and will be removed in the next major version of datasets. Use 'evaluate.load' instead, from the new library 🤗 Evaluate: https://huggingface.co/docs/evaluate
  cer_metric = load_metric("cer")
c:\Users\olver\anaconda3\envs\NS_env\Lib\site-packages\datasets\load.py:756: FutureWarning: The repository for cer contains custom code which must be executed to correctly load the metric. You can inspect the repository content at https://raw.githubusercontent.com/huggingface/datasets/2.18.0/metrics/cer/cer.py
You can avoid this message in future by passing the argument `trust_remote_code=True`.
Passing `trust_remote_code=True` will be mandatory to load this metric from the next major release of `datasets`.
  warnings.warn(
c:\Users\olver\anaconda3\envs\NS_env\Lib\site-packages\datasets\load.py:756: FutureWarning: The repository for wer contains custom code which must be executed to correctly

In [7]:
#cargamos el modelo preentrenado
model = AutoModelForSeq2SeqLM.from_pretrained(checkpoint)

In [8]:
# Definimos los argumentos de entrenamiento
training_args = Seq2SeqTrainingArguments(
    output_dir="sp_ay_translator",
    #eval_strategy="epoch",
    learning_rate=2e-3,
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    weight_decay=0.0001,
    save_total_limit=3,
    num_train_epochs=3,
    predict_with_generate=True,
    fp16=True,
    push_to_hub=True,
)

trainer = Seq2SeqTrainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_corpus["train"],
    eval_dataset=tokenized_corpus["test"],
    tokenizer=tokenizer,
    data_collator=data_collator,
    compute_metrics=compute_metrics,
)


c:\Users\olver\anaconda3\envs\NS_env\Lib\site-packages\accelerate\accelerator.py:432: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


In [9]:
# Entrenamos y evaluamos el modelo
trainer.train()
trainer.evaluate()

  0%|          | 0/3213 [00:00<?, ?it/s]

{'loss': 2.0331, 'grad_norm': 0.5498889088630676, 'learning_rate': 0.001689386865857454, 'epoch': 0.47}
{'loss': 1.6035, 'grad_norm': 0.6067703366279602, 'learning_rate': 0.0013781512605042017, 'epoch': 0.93}
{'loss': 1.4596, 'grad_norm': 0.6522427201271057, 'learning_rate': 0.0010669156551509494, 'epoch': 1.4}
{'loss': 1.3852, 'grad_norm': 0.48198166489601135, 'learning_rate': 0.0007556800497976969, 'epoch': 1.87}
{'loss': 1.3012, 'grad_norm': 0.7035029530525208, 'learning_rate': 0.0004444444444444444, 'epoch': 2.33}
{'loss': 1.2695, 'grad_norm': 0.6964818239212036, 'learning_rate': 0.000133208839091192, 'epoch': 2.8}
{'train_runtime': 4000.2069, 'train_samples_per_second': 6.423, 'train_steps_per_second': 0.803, 'train_loss': 1.4916166987628385, 'epoch': 3.0}


c:\Users\olver\anaconda3\envs\NS_env\Lib\site-packages\transformers\generation\utils.py:1132: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(


  0%|          | 0/189 [00:00<?, ?it/s]

{'eval_loss': 1.221753478050232,
 'eval_bleu': 0.1583,
 'eval_cer': 0.8668,
 'eval_wer': 0.9532,
 'eval_gen_len': 18.4861,
 'eval_runtime': 135.2724,
 'eval_samples_per_second': 11.177,
 'eval_steps_per_second': 1.397,
 'epoch': 3.0}

In [10]:
# Ejemplo de traducción
text = 'translate Spanish to Ayuuk: Hola, soy Alberto'
translator = pipeline("translation_xx_to_yy", model="sp_ay_translator")
translator(text)

[{'translation_text': 'ch, nm ja nm nm n'}]

In [15]:
from huggingface_hub import upload_folder

folder_path = "."

upload_folder(
    folder_path=folder_path,
    repo_id=f"{organization}/{repo_id}",
    commit_message="Subiendo modelo de traducción de español a ayuuk"
)


HfHubHTTPError: 403 Client Error: Forbidden for url: https://huggingface.co/l52mas/spanish_to_ayuuk_translator.git/info/lfs/objects/batch (Request ID: Root=1-673bd7f7-49fcc06606e2e5027608f8dc;05b34658-d5f9-4195-a245-09d560630b3d)

Authorization error.